In [1]:
from evolution_operators import *
from utility_functions import *

In [2]:
def evaluate_strategy(data, roc_period, rsi_period, roc_threshold, rsi_threshold, stop_loss_percentage):
    # Calculate indicators
    print(roc_period, rsi_period, roc_threshold, rsi_threshold, stop_loss_percentage)
#     data['MACD'], data['Signal'] = calculate_macd(data, fast_period, slow_period)
#     data['MACD_E'], data['Signal_E'] = calculate_macd(data, fast_p_exit, slow_p_exit)

    data['ROC'] = calculate_roc(data, roc_period)
    data['RSI_Derivative'] = talib.RSI(data['Close'], timeperiod=rsi_period)#calculate_rsi_derivative(data, rsi_period)
    
    # Apply trailing stop-loss exit condition
#     stop_loss = trailing_stop_loss(data, stop_loss_percentage)
    
    # Simulated trading logic
    position = 0  # 0 for no position, 1 for long position
    profit = 0
    total_trades = 0
    winning_trades = 0
    stop_loss_price = 0
    
    for i in range(1, len(data)):
        try:
            if data['ROC'][i] > roc_threshold :#and data['RSI_Derivative'][i] > rsi_threshold:
                if position == 0:
                    position = 1  # Buy (enter long position)
                    entry_price = data['Close'][i]
                    stop_loss_price = entry_price - (entry_price * 0.01 * stop_loss_percentage)
                    print(f"Entry: {entry_price} on {data.index[i]} Stop Loss: {stop_loss_price}")
                    total_trades += 1  
            elif position == 1:
                if data['Close'][i] > entry_price:  # Adjust stop loss only when the price goes up
                    stop_loss_price = max(stop_loss_price, data['Close'][i] - (data['Close'][i] * 0.01 * stop_loss_percentage))

                if data['Low'][i] < stop_loss_price:
                    position = 0  # Sell due to stop loss
                    exit_price = data['Open'][i] if stop_loss_price > data['Open'][i] else stop_loss_price
                    profit += exit_price - entry_price  # Calculate profit/loss
                    print(f"Exit: {exit_price} on {data.index[i]} exited on stop loss")
                    print(f"Profit: {profit}")
                    if(exit_price> entry_price):
                        winning_trades += 1
#                 elif data['MACD_E'][i] < data['Signal_E'][i]:
#                     position = 0  # Sell due to exit condition
#                     exit_price = data['Close'][i]
#                     profit += exit_price - entry_price  # Calculate profit/loss
#                     print(f"Exit: {exit_price} on {data.index[i]} exited on MACD condition")
#                     print(f"Profit: {profit}")
        except Exception as error:
            print("Something caused the error")
            print(error)
            break
        win_rate = winning_trades/total_trades if total_trades != 0 else 0
    
    return [profit,total_trades,winning_trades,win_rate]

In [8]:
# Fetch historical stock data
ticker_symbol = '^NSEI'  # Replace with your desired stock symbol
start_date = '2021-01-01'
end_date = '2022-12-31'
stock_data = fetch_stock_data(ticker_symbol, start_date, end_date)

# Genetic Algorithm parameters
population_size = 500
num_generations = 10
mutation_rate = 0.1
elite_size = 50
consecutive_threshold = 3  # Number of consecutive generations with no fitness improvement to consider saturation
fitness_history = []  # To store fitness scores across generations

# GA: Initialization

def generate_individual():

    return [random.randint(2,10),random.randint(2,10),random.randint(0,10), random.randint(0,99),random.randint(0,3)]

# Known or useful parameter values
known_parameters = [
    [4, 7, 0, 2,0], 
    [6, 2, 10, 26, 0]
    # Example set of known parameters
    # Add more known parameter sets if available
]

# Randomly generate the rest of the population
remaining_population = [generate_individual() for _ in range(population_size - len(known_parameters))]

# Initialize population using known parameter values and randomly generated values
population = known_parameters + remaining_population
# population = [generate_individual() for _ in range(population_size)]


for generation in range(num_generations):
    fitness_scores = [evaluate_strategy(stock_data.copy(), *individual)[0] for individual in population]
    sorted_population = [x for _, x in sorted(zip(fitness_scores, population), key=lambda pair: pair[0], reverse=True)]

    new_population = []

    # Select the top K individuals (elite) for the next generation
    elite = sorted_population[:elite_size]

        # Add fitness scores to the history
    fitness_history.append(max(fitness_scores))

    # Check for convergence or other stopping criteria

    #If convergence or stopping condition met, break the loop
    # Check for convergence or other stopping criteria
    if len(fitness_history) >= consecutive_threshold:
        recent_improvements = fitness_history[-consecutive_threshold:]
        if len(set(recent_improvements)) == 1:
            print("Saturation condition met, breaking the loop")
            break

    # Create new population by generating offspring from the elite individuals
    new_population = generate_offspring(elite,population_size,mutation_rate)

    population = new_population
    

# Find the best individual (parameters) from the final population
best_individual_index = np.argmax(fitness_scores)
best_individual = population[best_individual_index]
best_fitness_score = fitness_scores[best_individual_index]

print("Best Parameters:", best_individual)
print("Best Fitness Score:", best_fitness_score)


[*********************100%%**********************]  1 of 1 completed
4 7 0 2 0
Entry: 14137.349609375 on 2021-01-07 00:00:00 Stop Loss: 14137.349609375
Exit: 14433.7001953125 on 2021-01-15 00:00:00 exited on stop loss
Profit: 296.3505859375
Entry: 14644.7001953125 on 2021-01-20 00:00:00 Stop Loss: 14644.7001953125
Exit: 14477.7998046875 on 2021-01-25 00:00:00 exited on stop loss
Profit: 129.4501953125
Entry: 14281.2001953125 on 2021-02-01 00:00:00 Stop Loss: 14281.2001953125
Exit: 15118.9501953125 on 2021-02-18 00:00:00 exited on stop loss
Profit: 967.2001953125
Entry: 15097.349609375 on 2021-02-25 00:00:00 Stop Loss: 15097.349609375
Exit: 14888.599609375 on 2021-02-26 00:00:00 exited on stop loss
Profit: 758.4501953125
Entry: 14761.5498046875 on 2021-03-01 00:00:00 Stop Loss: 14761.5498046875
Exit: 14865.2998046875 on 2021-03-02 00:00:00 exited on stop loss
Profit: 862.2001953125
Entry: 15245.599609375 on 2021-03-03 00:00:00 Stop Loss: 15245.599609375
Exit: 15049.900390625 on 2021-03-

7 10 0 35 1
Entry: 14563.4501953125 on 2021-01-12 00:00:00 Stop Loss: 14417.815693359375
Exit: 14417.815693359375 on 2021-01-22 00:00:00 exited on stop loss
Profit: -145.63450195312544
Entry: 14647.849609375 on 2021-02-02 00:00:00 Stop Loss: 14501.37111328125
Exit: 14831.9325 on 2021-02-22 00:00:00 exited on stop loss
Profit: 38.448388671875364
Entry: 15245.599609375 on 2021-03-03 00:00:00 Stop Loss: 15093.14361328125
Exit: 14977.9501953125 on 2021-03-05 00:00:00 exited on stop loss
Profit: -229.20102539062464
Entry: 15098.400390625 on 2021-03-09 00:00:00 Stop Loss: 14947.41638671875
Exit: 14947.41638671875 on 2021-03-15 00:00:00 exited on stop loss
Profit: -380.18502929687384
Entry: 14845.099609375 on 2021-03-30 00:00:00 Stop Loss: 14696.64861328125
Exit: 14696.64861328125 on 2021-03-31 00:00:00 exited on stop loss
Profit: -528.6360253906241
Entry: 14867.349609375 on 2021-04-01 00:00:00 Stop Loss: 14718.67611328125
Exit: 14718.67611328125 on 2021-04-05 00:00:00 exited on stop loss
Pro

Entry: 15173.2998046875 on 2021-02-11 00:00:00 Stop Loss: 14869.83380859375
Exit: 15008.40619140625 on 2021-02-19 00:00:00 exited on stop loss
Profit: -164.8936132812505
Entry: 17315.5 on 2022-03-22 00:00:00 Stop Loss: 16969.19
Exit: 17692.3323828125 on 2022-04-07 00:00:00 exited on stop loss
Profit: 211.9387695312489
7 3 9 88 0
Entry: 15115.7998046875 on 2021-02-08 00:00:00 Stop Loss: 15115.7998046875
Exit: 15115.7998046875 on 2021-02-10 00:00:00 exited on stop loss
Profit: 0.0
6 4 4 74 1
Entry: 14895.650390625 on 2021-02-04 00:00:00 Stop Loss: 14746.69388671875
Exit: 15161.553193359376 on 2021-02-18 00:00:00 exited on stop loss
Profit: 265.90280273437565
Entry: 14894.900390625 on 2021-04-29 00:00:00 Stop Loss: 14745.95138671875
Exit: 14745.95138671875 on 2021-04-30 00:00:00 exited on stop loss
Profit: 116.95379882812631
Entry: 17323.599609375 on 2021-09-03 00:00:00 Stop Loss: 17150.36361328125
Exit: 17443.849609375 on 2021-09-20 00:00:00 exited on stop loss
Profit: 237.2037988281263


Entry: 15173.2998046875 on 2021-02-11 00:00:00 Stop Loss: 14718.100810546875
Exit: 14855.259189453125 on 2021-02-22 00:00:00 exited on stop loss
Profit: -318.04061523437485
Entry: 17315.5 on 2022-03-22 00:00:00 Stop Loss: 16796.035
Exit: 17511.79837890625 on 2022-04-12 00:00:00 exited on stop loss
Profit: -121.74223632812573
3 2 3 57 2
Entry: 14563.4501953125 on 2021-01-12 00:00:00 Stop Loss: 14272.18119140625
Exit: 14303.6876171875 on 2021-01-18 00:00:00 exited on stop loss
Profit: -259.7625781250008
Entry: 14647.849609375 on 2021-02-02 00:00:00 Stop Loss: 14354.8926171875
Exit: 15008.40619140625 on 2021-02-19 00:00:00 exited on stop loss
Profit: 100.79400390624869
Entry: 15245.599609375 on 2021-03-03 00:00:00 Stop Loss: 14940.6876171875
Exit: 14940.6876171875 on 2021-03-05 00:00:00 exited on stop loss
Profit: -204.1179882812521
Entry: 14864.5498046875 on 2021-04-28 00:00:00 Stop Loss: 14567.25880859375
Exit: 14481.0498046875 on 2021-05-03 00:00:00 exited on stop loss
Profit: -587.617

Exit: 17283.19921875 on 2021-12-14 00:00:00 exited on stop loss
Profit: 145.6544824218745
Entry: 17003.75 on 2021-12-24 00:00:00 Stop Loss: 16833.7125
Exit: 17931.9202734375 on 2022-01-19 00:00:00 exited on stop loss
Profit: 1073.824755859374
Entry: 17339.849609375 on 2022-01-31 00:00:00 Stop Loss: 17166.45111328125
Exit: 17166.45111328125 on 2022-02-07 00:00:00 exited on stop loss
Profit: 900.4262597656252
Entry: 17276.30078125 on 2022-02-18 00:00:00 Stop Loss: 17103.5377734375
Exit: 17103.5377734375 on 2022-02-21 00:00:00 exited on stop loss
Profit: 727.6632519531249
Entry: 16498.05078125 on 2022-03-03 00:00:00 Stop Loss: 16333.0702734375
Exit: 16333.0702734375 on 2022-03-04 00:00:00 exited on stop loss
Profit: 562.6827441406258
Entry: 16594.900390625 on 2022-03-10 00:00:00 Stop Loss: 16428.95138671875
Exit: 17050.5225 on 2022-03-28 00:00:00 exited on stop loss
Profit: 1018.3048535156249
Entry: 17498.25 on 2022-03-30 00:00:00 Stop Loss: 17323.2675
Exit: 17606.50611328125 on 2022-04-0

...

Exit: 14433.7001953125 on 2021-01-15 00:00:00 exited on stop loss
Profit: 287.4501953125
Entry: 14644.7001953125 on 2021-01-20 00:00:00 Stop Loss: 14644.7001953125
Exit: 14583.400390625 on 2021-01-22 00:00:00 exited on stop loss
Profit: 226.150390625
Entry: 14281.2001953125 on 2021-02-01 00:00:00 Stop Loss: 14281.2001953125
Exit: 15118.9501953125 on 2021-02-18 00:00:00 exited on stop loss
Profit: 1063.900390625
Entry: 14982.0 on 2021-02-24 00:00:00 Stop Loss: 14982.0
Exit: 14888.599609375 on 2021-02-26 00:00:00 exited on stop loss
Profit: 970.5
Entry: 15245.599609375 on 2021-03-03 00:00:00 Stop Loss: 15245.599609375
Exit: 15002.4501953125 on 2021-03-08 00:00:00 exited on stop loss
Profit: 727.3505859375
Entry: 15098.400390625 on 2021-03-09 00:00:00 Stop Loss: 15098.400390625
Exit: 15048.400390625 on 2021-03-15 00:00:00 exited on stop loss
Profit: 677.3505859375
Entry: 14736.400390625 on 2021-03-22 00:00:00 Stop Loss: 14736.400390625
Exit: 14712.4501953125 on 2021-03-24 00:00:00 exited 

Profit: 4151.400390625
Entry: 17798.75 on 2022-09-08 00:00:00 Stop Loss: 17798.75
Exit: 17796.80078125 on 2022-09-16 00:00:00 exited on stop loss
Profit: 4149.451171875
Entry: 17185.69921875 on 2022-10-14 00:00:00 Stop Loss: 17185.69921875
Exit: 18159.94921875 on 2022-11-21 00:00:00 exited on stop loss
Profit: 5123.701171875
Entry: 18484.099609375 on 2022-11-24 00:00:00 Stop Loss: 18484.099609375
Exit: 18512.75 on 2022-11-25 00:00:00 exited on stop loss
Profit: 5152.3515625
Entry: 18562.75 on 2022-11-28 00:00:00 Stop Loss: 18562.75
Exit: 18570.849609375 on 2022-12-08 00:00:00 exited on stop loss
Profit: 5160.451171875
8 8 1 69 0
Entry: 14564.849609375 on 2021-01-13 00:00:00 Stop Loss: 14564.849609375
Exit: 14453.2998046875 on 2021-01-18 00:00:00 exited on stop loss
Profit: -111.5498046875
Entry: 14521.150390625 on 2021-01-19 00:00:00 Stop Loss: 14521.150390625
Exit: 14590.349609375 on 2021-01-21 00:00:00 exited on stop loss
Profit: -42.3505859375
Entry: 14789.9501953125 on 2021-02-03 0

Exit: 18113.05078125 on 2022-01-18 00:00:00 exited on stop loss
Profit: 2924.3515625
Entry: 17339.849609375 on 2022-01-31 00:00:00 Stop Loss: 17339.849609375
Exit: 17516.30078125 on 2022-02-04 00:00:00 exited on stop loss
Profit: 3100.802734375
Entry: 17605.849609375 on 2022-02-10 00:00:00 Stop Loss: 17605.849609375
Exit: 17076.150390625 on 2022-02-14 00:00:00 exited on stop loss
Profit: 2571.103515625
Entry: 17304.599609375 on 2022-02-17 00:00:00 Stop Loss: 17304.599609375
Exit: 17236.05078125 on 2022-02-18 00:00:00 exited on stop loss
Profit: 2502.5546875
Entry: 16605.94921875 on 2022-03-02 00:00:00 Stop Loss: 16605.94921875
Exit: 16605.94921875 on 2022-03-03 00:00:00 exited on stop loss
Profit: 2502.5546875
Entry: 16345.349609375 on 2022-03-09 00:00:00 Stop Loss: 16345.349609375
Exit: 17245.650390625 on 2022-03-23 00:00:00 exited on stop loss
Profit: 3402.85546875
Entry: 17222.75 on 2022-03-24 00:00:00 Stop Loss: 17222.75
Exit: 17222.75 on 2022-03-25 00:00:00 exited on stop loss
Pro

Entry: 17790.349609375 on 2021-10-07 00:00:00 Stop Loss: 17790.349609375
Exit: 18114.900390625 on 2021-10-22 00:00:00 exited on stop loss
Profit: 3056.6015625
Entry: 17916.80078125 on 2021-11-04 00:00:00 Stop Loss: 17916.80078125
Exit: 17999.19921875 on 2021-11-16 00:00:00 exited on stop loss
Profit: 3139.0
Entry: 17196.69921875 on 2021-12-03 00:00:00 Stop Loss: 17196.69921875
Exit: 17196.69921875 on 2021-12-06 00:00:00 exited on stop loss
Profit: 3139.0
Entry: 17176.69921875 on 2021-12-07 00:00:00 Stop Loss: 17176.69921875
Exit: 17221.400390625 on 2021-12-15 00:00:00 exited on stop loss
Profit: 3183.701171875
Entry: 17003.75 on 2021-12-24 00:00:00 Stop Loss: 17003.75
Exit: 17938.400390625 on 2022-01-19 00:00:00 exited on stop loss
Profit: 4118.3515625
Entry: 17576.849609375 on 2022-02-01 00:00:00 Stop Loss: 17576.849609375
Exit: 17456.30078125 on 2022-02-07 00:00:00 exited on stop loss
Profit: 3997.802734375
Entry: 17605.849609375 on 2022-02-10 00:00:00 Stop Loss: 17605.849609375
Exit

Exit: 14653.0498046875 on 2021-05-04 00:00:00 exited on stop loss
Profit: 788.8515625
Entry: 14823.150390625 on 2021-05-07 00:00:00 Stop Loss: 14823.150390625
Exit: 14749.400390625 on 2021-05-14 00:00:00 exited on stop loss
Profit: 715.1015625
Entry: 14923.150390625 on 2021-05-17 00:00:00 Stop Loss: 14923.150390625
Exit: 15648.2998046875 on 2021-06-17 00:00:00 exited on stop loss
Profit: 1440.2509765625
Entry: 15790.4501953125 on 2021-06-24 00:00:00 Stop Loss: 15790.4501953125
Exit: 15790.4501953125 on 2021-06-29 00:00:00 exited on stop loss
Profit: 1440.2509765625
Entry: 15721.5 on 2021-06-30 00:00:00 Stop Loss: 15721.5
Exit: 15721.5 on 2021-07-01 00:00:00 exited on stop loss
Profit: 1440.2509765625
Entry: 15834.349609375 on 2021-07-05 00:00:00 Stop Loss: 15834.349609375
Exit: 15688.25 on 2021-07-09 00:00:00 exited on stop loss
Profit: 1294.1513671875
Entry: 15924.2001953125 on 2021-07-15 00:00:00 Stop Loss: 15924.2001953125
Exit: 15703.9501953125 on 2021-07-20 00:00:00 exited on stop

In [7]:
stock_data = yf.download("DLF.NS", start='2023-01-01',end='2023-12-28')

# Use the best parameters obtained from the GA
#"Best Parameters (Fast Period, Slow Period, ROC Period, RSI Period, ROC Threshold, RSI Derivative Threshold, Stop Loss %):"
best_parameters = [7, 4, 0, 40, 0]

# Apply the strategy on out-of-sample data using the best parameters
out_of_sample_profit = evaluate_strategy(stock_data.copy(), *best_parameters)


# Print or analyze the performance metrics
print("Out-of-sample profit:", out_of_sample_profit)

[*********************100%%**********************]  1 of 1 completed
7 4 0 40 0
Entry: 377.04998779296875 on 2023-01-13 00:00:00 Stop Loss: 377.04998779296875
Exit: 374.0 on 2023-01-20 00:00:00 exited on stop loss
Profit: -3.04998779296875
Entry: 353.8999938964844 on 2023-02-06 00:00:00 Stop Loss: 353.8999938964844
Exit: 357.5 on 2023-02-21 00:00:00 exited on stop loss
Profit: 0.550018310546875
Entry: 360.25 on 2023-03-03 00:00:00 Stop Loss: 360.25
Exit: 355.1000061035156 on 2023-03-10 00:00:00 exited on stop loss
Profit: -4.5999755859375
Entry: 360.04998779296875 on 2023-03-16 00:00:00 Stop Loss: 360.04998779296875
Exit: 355.20001220703125 on 2023-03-27 00:00:00 exited on stop loss
Profit: -9.449951171875
Entry: 382.8999938964844 on 2023-04-06 00:00:00 Stop Loss: 382.8999938964844
Exit: 410.04998779296875 on 2023-04-25 00:00:00 exited on stop loss
Profit: 17.700042724609375
Entry: 416.6000061035156 on 2023-04-26 00:00:00 Stop Loss: 416.6000061035156
Exit: 416.54998779296875 on 2023-04

In [21]:
stock_data['ROC'] = calculate_roc(stock_data, 4)
stock_data['RSI_Derivative'] = calculate_rsi_derivative(stock_data, 3)

In [22]:
best_individual_index = np.argmax(fitness_scores)
best_individual = population[best_individual_index]
best_fitness_score = fitness_scores[best_individual_index]
print("Best Parameters:", best_individual)
print("Best Fitness Score:", best_fitness_score)


Best Parameters: [5, 3, 6, 51, 0]
Best Fitness Score: 3862.2998046875
